## Libraries

In [32]:
# Import necessary libraries
import pandas as pd
import numpy as np
from datetime import datetime
from os.path import join
import os
from pathlib import Path
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from scipy.ndimage import gaussian_filter
from statsmodels.nonparametric.smoothers_lowess import lowess

path_cwd=Path.cwd()
path_input=str(path_cwd)+'/Data_input/'


## Functions

In [33]:

# Function to read and process a single file
def read_and_process_single(file_path, cols, start_date):#, end_date):
    DFr = pd.read_csv(file_path, header=None, skiprows=1, names=cols, engine='python', encoding="ISO-8859-1")
    DF = DFr[~DFr['Date'].str.contains("[a-zA-Z]").fillna(False)].dropna(subset=['Date'])
    ind1 = pd.to_datetime(DF['Date'] + ' ' + DF['Time'], errors='coerce', format='%Y-%d-%m %H:%M:%S')
    ind2 = pd.to_datetime(DF['Date'] + ' ' + DF['Time'], errors='coerce', format='%d/%m/%Y %H:%M:%S')
    DF.index = ind1.fillna(ind2)
    DF = DF[(DF.index >= start_date) ]#& (DF.index < end_date)]
    DF=DF.drop(columns=['Date','Time','Intercept','Slope','EDBO','Correction for dT','Correction Factor','IBV','IBT','EPS Present','EPS Voltage','EPS Current','Diagnostic Comment','NA']) #If we want diagnostic for something: 'Date','Time','IBV','IBT','EPS Present','EPS Voltage','EPS Current','Diagnostic Comment','NA'


    DF=DF.apply(lambda x: pd.to_numeric(x, errors='coerce')) #Convert argument to a numeric type.
    DF=DF.astype({'Chamber Temperature':'float','dT':'float','Wet Bulb Depression':'float','Corrected Water Potential':'float'})#,'Intercept':'float','Slope':'float','EDBO':'float','Correction for dT':'float','Correction Factor':'float'}) #specify the numeric type in this case float 
    DF.columns=['Chamber Temperature (C)','dT (C)','Wet Bulb Depression','Corrected Water Potential (MPa)']

    DF.index=DF.index.floor('0.5H') #round 
    DF=DF[~DF.index.duplicated(keep='first')] # keep everything but the duplicated values
    DF=DF.asfreq('30 min') #resample with a nan so gaps are not ploted as a weird interpolation

    return DF


# Data Cleaning Function
def clean_data(df):
    # Replace zeros with NaN
    df.replace(0, np.nan, inplace=True)

    # Handling spikes or other specific cleaning requirements-this can include removing sudden peaks or smoothing the data
    threshold = 10  #Remove values that differ from their neighbors beyond a threshold

    for i in range(1, len(df) - 1):
        if abs(df.iloc[i] - df.iloc[i-1]) > threshold and abs(df.iloc[i] - df.iloc[i+1]) > threshold:
            df.iloc[i] = np.nan

    return df

def lowess_data(df): #Locally Weighted Scatterplot Smoothing
    frac=0.09
    # Apply LOWESS smoothing to the data
    # frac is the fraction of data points used when estimating each y value
    df_lowess = lowess(df.dropna(), df.dropna().index, frac=frac, return_sorted=False)
    
    # The lowess function returns a numpy array, so we convert it back to a Series
    df_smooth = pd.Series(df_lowess, index=df.dropna().index)
    
    # Reindex to the original index with NaNs for missing values
    df_smooth = df_smooth.reindex(df.index)

    return df_smooth

# Segmentation Function
def segment_series(series, max_gap):
    """
    Segments the Series based on the maximum allowed gap (max_gap) of NaNs.
    
    Args:
    series (Series): Time series data.
    max_gap (int): Maximum allowed gap of consecutive NaNs.

    Returns:
    List of Series, each representing a segment.
    """
    segments = []
    segment = []
    gap = 0

    for index, value in series.items():
        if pd.isna(value):
            gap += 1
            if gap > max_gap:
                if segment:
                    segments.append(pd.Series(segment, index=[idx for idx, _ in segment]))
                    segment = []
            else:
                segment.append((index, value))
        else:
            gap = 0
            segment.append((index, value))

    if segment:
        segments.append(pd.Series(segment, index=[idx for idx, _ in segment]))
    
    return segments


## Reading and cropping

In [34]:
input_files_path=path_input+'inputfiles.csv'
input_files_df = pd.read_csv(input_files_path)

# Column names for the data files (update as needed)
PSY_cols = ['Date', 'Time', 'Chamber Temperature', 'dT', 'Wet Bulb Depression', 'Corrected Water Potential', 'Intercept', 'Slope', 'EDBO', 'Correction for dT', 'Correction Factor', 'IBV', 'IBT', 'EPS Present', 'EPS Voltage', 'EPS Current', 'Diagnostic Comment', 'NA']

# Process each file according to its type
trees_data = {} #trees_data dictionary now contains the processed data for each tree
#end_date = datetime.strptime('2022-10-21 00:00:00', '%Y-%m-%d %H:%M:%S')
for index, row in input_files_df.iterrows():
    filename = row['Filename']
    tree = row['Tree']
    start_date = datetime.strptime(row['Start_date'], '%Y-%m-%d %H:%M')
    reading_type = row['Reading']

    file_path = join(path_input, filename)  # Update with the correct path
    trees_data[tree] = read_and_process_single(file_path, PSY_cols, start_date) #,end_date)

## Cleaning data 

In [35]:
for tree, df in trees_data.items():
    original_data = df['Corrected Water Potential (MPa)'].copy()  
    cleaned_data = clean_data(original_data) # remove zeros and peaks with function 

    #smoothing noise
    smooth = pd.Series(gaussian_filter(cleaned_data.copy(),1)) #change sigma to change the smoothing s=0.5,2
    smooth.index = cleaned_data.index

    shape_data = smooth.copy() 
    shape_data = lowess_data(shape_data) #Locally Weighted Scatterplot Smoothing
    

    # Store both original and cleaned data in the dictionary
    trees_data[tree] = {
        'Original Corrected Water Potential (MPa)': df['Corrected Water Potential (MPa)'].copy(),
        'Cleaned Corrected Water Potential (MPa)': cleaned_data,
        'Smoothed Corrected Water Potential (MPa)': smooth,
        'Shape of overall behavior': shape_data
    }

In [36]:
fig = go.Figure()
for tree, df in trees_data.items():
    fig.add_trace(go.Scatter(x=df['Shape of overall behavior'].index, y=df['Shape of overall behavior'], name=tree, mode='lines', line=dict(width=1)))
#fig.show()

In [37]:
#PLOT THE CLEANED VS THE ORIGINAL DATA
# Determine the number of trees (subplots) to create
num_trees = len(trees_data)
fig = make_subplots(rows=num_trees, cols=1, subplot_titles=list(trees_data.keys()))

# Looping through each tree's data to create subplots
for i, (tree, df) in enumerate(trees_data.items(), start=1):
    # Original Data
    fig.add_trace(
        go.Scatter(x=df['Original Corrected Water Potential (MPa)'].index, y=df['Original Corrected Water Potential (MPa)'], 
                   mode='lines', name=f'{tree} Original', legendgroup=tree),
        row=i, col=1
    )

    # Cleaned and smoothed Data
    fig.add_trace(
        go.Scatter(x=df['Smoothed Corrected Water Potential (MPa)'].index, y=df['Smoothed Corrected Water Potential (MPa)'], 
                   mode='lines', name=f'{tree} Cleaned and smoothed', legendgroup=tree),
        row=i, col=1
    )

# Update layout
fig.update_layout(height=300*num_trees, width=1000, title_text="Original vs Cleaned Data for Each Tree")
fig.show()


## Interpolation

### Linear (classic interpolation methods)

In [39]:
# TRIAL FOR DIFFERENT SMOOTH OPTIONS WITH LINEAR INTERPOLATION
num_trees = len(trees_data)
fig = make_subplots(rows=num_trees, cols=1, subplot_titles=list(trees_data.keys()))

for i, (tree, df) in enumerate(trees_data.items(), start=1):
    #SMOOTH DATA   
    original_data = df['Cleaned Corrected Water Potential (MPa)'].copy()  # Assuming this is your original column
    smooth_p5 = pd.Series(gaussian_filter(original_data.copy(),0.5))
    smooth_1 = pd.Series(gaussian_filter(original_data.copy(),1))
    smooth_2 = pd.Series(gaussian_filter(original_data.copy(),2))

    #INTERPOLATION over Gaussian kernel 1 SD interpolation

    interpolation_choice = smooth_1   
    interpolation_choice.index = original_data.index
    nighttime_condition = (interpolation_choice.index.hour >= 22.0) | (interpolation_choice.index.hour < 9)
    daytime_condition = ~nighttime_condition
    interpolation_limit_night = 12
    interpolation_limit_day = 4

    #linear interpolation
    interpolation_linear = interpolation_choice.copy()
    interpolation_linear.loc[nighttime_condition]=interpolation_linear.loc[nighttime_condition].interpolate(method='linear', limit_direction='both',limit=interpolation_limit_night)
    interpolation_linear.loc[daytime_condition]=interpolation_linear.loc[daytime_condition].interpolate(method='linear', limit_direction='both',limit=interpolation_limit_day)

    # #cubic interpolation (not recommended- gets positive values)
    # interpolation_cubic = interpolation_choice.copy()
    # interpolation_cubic.loc[nighttime_condition]=interpolation_cubic.loc[nighttime_condition].interpolate(method='cubic', limit_direction='both',limit=interpolation_limit_night)
    # interpolation_cubic.loc[daytime_condition]=interpolation_cubic.loc[daytime_condition].interpolate(method='cubic', limit_direction='both',limit=interpolation_limit_day)

    # #quadratic interpolation (not recommended- gets positive values)
    # interpolation_quadratic = interpolation_choice.copy()
    # interpolation_quadratic.loc[nighttime_condition]=interpolation_quadratic.loc[nighttime_condition].interpolate(method='quadratic', limit_direction='both',limit=interpolation_limit_night)
    # interpolation_quadratic.loc[daytime_condition]=interpolation_quadratic.loc[daytime_condition].interpolate(method='quadratic', limit_direction='both',limit=interpolation_limit_day)

    # fig.add_trace(
    #     go.Scatter(x=original_data.index, y=original_data, 
    #                mode='lines', name=f'{tree} Original', legendgroup=tree),
    #     row=i, col=1
    # )

    # fig.add_trace(
    #     go.Scatter(x=interpolation_choice.index, y=interpolation_choice,
    #                  mode='lines', name=f'{tree} Smoothed', legendgroup=tree),
    #     row=i, col=1
    # )

    # fig.add_trace(
    #     go.Scatter(x=interpolation_linear.index, y=interpolation_linear, 
    #                mode='lines', name=f'{tree} Interpolated linear', legendgroup=tree),
    #     row=i, col=1
    # )


# fig.update_layout(height=300*num_trees, width=1000, title_text="Cleaned vs Smoothed Data for Each Tree")
# fig.show()
    